In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np 
import pandas as pd 
import json 

from subprocess import check_output

In [2]:
def squad_json_to_dataframe_train(input_file_path, record_path = ['data','paragraphs','qas','answers'],
                           verbose = 1):
    """
    input_file_path: path to the squad json file.
    record_path: path to deepest level in json file default value is
    ['data','paragraphs','qas','answers']
    verbose: 0 to suppress it default is 1
    """
    if verbose:
        print("Reading the json file")    
    file = json.loads(open(input_file_path).read())
    if verbose:
        print("processing...")
    # parsing different level's in the json file
    js = pd.json_normalize(file , record_path )
    m = pd.json_normalize(file, record_path[:-1] )
    r = pd.json_normalize(file,record_path[:-2])
    
    #combining it into single dataframe
    idx = np.repeat(r['context'].values, r.qas.str.len())
    ndx  = np.repeat(m['id'].values,m['answers'].str.len())
    m['context'] = idx
    js['q_idx'] = ndx
    main = pd.concat([m[['id','question','context']].set_index('id'), js.set_index('q_idx')], axis=1, sort=False).reset_index()
    main['c_id'] = main['context'].factorize()[0]
    if verbose:
        print("shape of the dataframe is {}".format(main.shape))
        print("Done")
    return main

We have to define a different fuctions for Dev data because the the dev data is slightly different mainly there are multiple possible answer for a single question

In [3]:
def squad_json_to_dataframe_dev(input_file_path, record_path = ['data','paragraphs','qas','answers'],
                           verbose = 1):
    """
    input_file_path: path to the squad json file.
    record_path: path to deepest level in json file default value is
    ['data','paragraphs','qas','answers']
    verbose: 0 to suppress it default is 1
    """
    if verbose:
        print("Reading the json file")    
    file = json.loads(open(input_file_path).read())
    if verbose:
        print("processing...")
    # parsing different level's in the json file
    js = pd.json_normalize(file , record_path )
    m = pd.json_normalize(file, record_path[:-1] )
    r = pd.json_normalize(file,record_path[:-2])
    
    #combining it into single dataframe
    idx = np.repeat(r['context'].values, r.qas.str.len())
#     ndx  = np.repeat(m['id'].values,m['answers'].str.len())
    m['context'] = idx
#     js['q_idx'] = ndx
    main = m[['id','question','context','answers']].set_index('id').reset_index()
    main['c_id'] = main['context'].factorize()[0]
    if verbose:
        print("shape of the dataframe is {}".format(main.shape))
        print("Done")
    return main

In [4]:
# training data
input_file_path = 'train-v1.1.json'
record_path = ['data','paragraphs','qas','answers']
train = squad_json_to_dataframe_train(input_file_path=input_file_path,record_path=record_path)

Reading the json file
processing...
shape of the dataframe is (87599, 6)
Done


In [5]:
train.head()

index  \
0  5733be284776f41900661182   
1  5733be284776f4190066117f   
2  5733be284776f41900661180   
3  5733be284776f41900661181   
4  5733be284776f4190066117e   

                                            question  \
0  To whom did the Virgin Mary allegedly appear i...   
1  What is in front of the Notre Dame Main Building?   
2  The Basilica of the Sacred heart at Notre Dame...   
3                  What is the Grotto at Notre Dame?   
4  What sits on top of the Main Building at Notre...   

                                             context  answer_start  \
0  Architecturally, the school has a Catholic cha...           515   
1  Architecturally, the school has a Catholic cha...           188   
2  Architecturally, the school has a Catholic cha...           279   
3  Architecturally, the school has a Catholic cha...           381   
4  Architecturally, the school has a Catholic cha...            92   

                                      text  c_id  
0               Saint Bernadette Soubirous     0  
1                a copper statue of Christ     0  
2                        the Main Building     0  
3  a Marian place of prayer and reflection     0  
4       a golden statue of the Virgin Mary     0

In [6]:
# dev data
input_file_path = 'dev-v1.1.json'
record_path = ['data','paragraphs','qas','answers']
verbose = 0
dev = squad_json_to_dataframe_dev(input_file_path=input_file_path,record_path=record_path)

Reading the json file
processing...
shape of the dataframe is (10570, 5)
Done


In [7]:
dev.head()

id  \
0  56be4db0acb8001400a502ec   
1  56be4db0acb8001400a502ed   
2  56be4db0acb8001400a502ee   
3  56be4db0acb8001400a502ef   
4  56be4db0acb8001400a502f0   

                                            question  \
0  Which NFL team represented the AFC at Super Bo...   
1  Which NFL team represented the NFC at Super Bo...   
2                Where did Super Bowl 50 take place?   
3                  Which NFL team won Super Bowl 50?   
4  What color was used to emphasize the 50th anni...   

                                             context  \
0  Super Bowl 50 was an American football game to...   
1  Super Bowl 50 was an American football game to...   
2  Super Bowl 50 was an American football game to...   
3  Super Bowl 50 was an American football game to...   
4  Super Bowl 50 was an American football game to...   

                                             answers  c_id  
0  [{'answer_start': 177, 'text': 'Denver Broncos...     0  
1  [{'answer_start': 249, 'text': 'Carolina Panth...     0  
2  [{'answer_start': 403, 'text': 'Santa Clara, C...     0  
3  [{'answer_start': 177, 'text': 'Denver Broncos...     0  
4  [{'answer_start': 488, 'text': 'gold'}, {'answ...     0

In [8]:
data = pd.DataFrame(dev)

In [9]:
print(data)

                             id  \
0      56be4db0acb8001400a502ec   
1      56be4db0acb8001400a502ed   
2      56be4db0acb8001400a502ee   
3      56be4db0acb8001400a502ef   
4      56be4db0acb8001400a502f0   
...                         ...   
10565  5737aafd1c456719005744fb   
10566  5737aafd1c456719005744fc   
10567  5737aafd1c456719005744fd   
10568  5737aafd1c456719005744fe   
10569  5737aafd1c456719005744ff   

                                                question  \
0      Which NFL team represented the AFC at Super Bo...   
1      Which NFL team represented the NFC at Super Bo...   
2                    Where did Super Bowl 50 take place?   
3                      Which NFL team won Super Bowl 50?   
4      What color was used to emphasize the 50th anni...   
...                                                  ...   
10565  What is the metric term less used than the New...   
10566  What is the kilogram-force sometimes reffered ...   
10567  What is a very seldom used unit 

In [12]:
print(data)

                             id  \
0      56be4db0acb8001400a502ec   
1      56be4db0acb8001400a502ed   
2      56be4db0acb8001400a502ee   
3      56be4db0acb8001400a502ef   
4      56be4db0acb8001400a502f0   
...                         ...   
10565  5737aafd1c456719005744fb   
10566  5737aafd1c456719005744fc   
10567  5737aafd1c456719005744fd   
10568  5737aafd1c456719005744fe   
10569  5737aafd1c456719005744ff   

                                                question  \
0      Which NFL team represented the AFC at Super Bo...   
1      Which NFL team represented the NFC at Super Bo...   
2                    Where did Super Bowl 50 take place?   
3                      Which NFL team won Super Bowl 50?   
4      What color was used to emphasize the 50th anni...   
...                                                  ...   
10565  What is the metric term less used than the New...   
10566  What is the kilogram-force sometimes reffered ...   
10567  What is a very seldom used unit 

In [10]:
train_data = pd.DataFrame(train)

In [11]:
train_data.to_csv('train_data.csv', index=False)

In [12]:
import pandas as pd
data = data.drop(columns=['id'])
print(data.head())


                                            question  \
0  Which NFL team represented the AFC at Super Bo...   
1  Which NFL team represented the NFC at Super Bo...   
2                Where did Super Bowl 50 take place?   
3                  Which NFL team won Super Bowl 50?   
4  What color was used to emphasize the 50th anni...   

                                             context  \
0  Super Bowl 50 was an American football game to...   
1  Super Bowl 50 was an American football game to...   
2  Super Bowl 50 was an American football game to...   
3  Super Bowl 50 was an American football game to...   
4  Super Bowl 50 was an American football game to...   

                                             answers  c_id  
0  [{'answer_start': 177, 'text': 'Denver Broncos...     0  
1  [{'answer_start': 249, 'text': 'Carolina Panth...     0  
2  [{'answer_start': 403, 'text': 'Santa Clara, C...     0  
3  [{'answer_start': 177, 'text': 'Denver Broncos...     0  
4  [{'answer_start': 

In [22]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import FeatureUnion
from scipy.sparse import hstack

ImportError: cannot import name 'fastCopyAndTranspose' from 'numpy.core._multiarray_umath' (c:\Users\KATANA\AppData\Local\Programs\Python\Python311\Lib\site-packages\numpy\core\_multiarray_umath.py)

In [15]:
import pandas as pd
import tensorflow as tf
from tensorflow.keras.layers import TextVectorization
from scipy.sparse import hstack

# Sample data - replace with your actual data
data = {'id': [1, 2, 3], 'question': ['What is AI?', 'How does machine learning work?', 'Explain neural networks.'], 'context': ['AI is the study of intelligent agents.', 'Machine learning is a subset of AI.', 'Neural networks are inspired by the human brain.']}
df = pd.DataFrame(data)

# Initialize TextVectorization layers
question_vectorizer = TextVectorization(max_tokens=5000, ngrams=2, standardize=None, split='whitespace', pad_to_max_tokens=True)
context_vectorizer = TextVectorization(max_tokens=5000, ngrams=2, standardize=None, split='whitespace', pad_to_max_tokens=True)

# Convert data to TensorFlow dataset
def create_tf_dataset(data):
    return tf.data.Dataset.from_tensor_slices(data).batch(len(data))

# Prepare the TextVectorization layers
question_dataset = create_tf_dataset(df['question'].tolist())
context_dataset = create_tf_dataset(df['context'].tolist())

question_vectorizer.adapt(question_dataset)
context_vectorizer.adapt(context_dataset)

# Transform the 'question' and 'context' fields
question_features = question_vectorizer(tf.constant(df['question'].tolist()))
context_features = context_vectorizer(tf.constant(df['context'].tolist()))

# Convert to dense format
question_features_dense = question_features.numpy()
context_features_dense = context_features.numpy()

# Combine features
combined_features = hstack([question_features_dense, context_features_dense])

# Convert combined features to a DataFrame
combined_feature_df = pd.DataFrame(combined_features, columns=[f'feature_{i}' for i in range(combined_features.shape[1])])

# Add the original 'id' to the new DataFrame
final_df = pd.concat([df[['id']], combined_feature_df], axis=1)

# Print the final DataFrame
print(final_df)


ValueError: could not broadcast input array from shape (3,9) into shape (3,)

In [15]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from scipy.sparse import hstack

df = pd.DataFrame(data)

# Initialize TF-IDF Vectorizers with different settings
question_tfidf = TfidfVectorizer(max_features=5000, stop_words=None, ngram_range=(1, 2))
context_tfidf = TfidfVectorizer(max_features=5000, stop_words=None, ngram_range=(1, 2))

# Fit and transform the 'question' and 'context' fields
question_features = question_tfidf.fit_transform(df['question'])
context_features = context_tfidf.fit_transform(df['context'])

# Combine the features
combined_features = hstack([question_features, context_features])

# Convert combined features to a DataFrame
combined_feature_df = pd.DataFrame(combined_features.toarray(), columns=[f'feature_{i}' for i in range(combined_features.shape[1])])

# Add the original 'id' to the new DataFrame
final_df = pd.concat([combined_feature_df], axis=1)

# Print the final DataFrame
print(final_df)


       feature_0  feature_1  feature_2  feature_3  feature_4  feature_5  \
0            0.0        0.0        0.0        0.0        0.0        0.0   
1            0.0        0.0        0.0        0.0        0.0        0.0   
2            0.0        0.0        0.0        0.0        0.0        0.0   
3            0.0        0.0        0.0        0.0        0.0        0.0   
4            0.0        0.0        0.0        0.0        0.0        0.0   
...          ...        ...        ...        ...        ...        ...   
10565        0.0        0.0        0.0        0.0        0.0        0.0   
10566        0.0        0.0        0.0        0.0        0.0        0.0   
10567        0.0        0.0        0.0        0.0        0.0        0.0   
10568        0.0        0.0        0.0        0.0        0.0        0.0   
10569        0.0        0.0        0.0        0.0        0.0        0.0   

       feature_6  feature_7  feature_8  feature_9  ...  feature_9990  \
0            0.0        0.0

In [16]:
df_train = pd.DataFrame(train_data)

# Initialize TF-IDF Vectorizers for 'question' and 'context'
question_tfidf_train = TfidfVectorizer(max_features=1000, stop_words='english')
context_tfidf_train = TfidfVectorizer(max_features=1000, stop_words='english')

# Fit and transform the 'question' and 'context' fields
question_features_train = question_tfidf_train.fit_transform(df['question'])
context_features_train = context_tfidf_train.fit_transform(df['context'])

# Combine the features
combined_features_train = hstack([question_features_train, context_features_train])

# Output the TF-IDF features
print(combined_features_train.toarray())

# To see feature names (if needed)
question_feature_names_train = question_tfidf_train.get_feature_names_out()
context_feature_names_train = context_tfidf_train.get_feature_names_out()


[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


In [17]:
combined_features = hstack([question_features, context_features])

# Convert combined features to a DataFrame
combined_feature_df = pd.DataFrame(combined_features.toarray(), columns=[f'feature_{i}' for i in range(combined_features.shape[1])])

# Add the original 'id' to the new DataFrame
final_df = pd.concat([combined_feature_df], axis=1)

# Print the final DataFrame
print(final_df)

       feature_0  feature_1  feature_2  feature_3  feature_4  feature_5  \
0            0.0        0.0        0.0        0.0        0.0        0.0   
1            0.0        0.0        0.0        0.0        0.0        0.0   
2            0.0        0.0        0.0        0.0        0.0        0.0   
3            0.0        0.0        0.0        0.0        0.0        0.0   
4            0.0        0.0        0.0        0.0        0.0        0.0   
...          ...        ...        ...        ...        ...        ...   
10565        0.0        0.0        0.0        0.0        0.0        0.0   
10566        0.0        0.0        0.0        0.0        0.0        0.0   
10567        0.0        0.0        0.0        0.0        0.0        0.0   
10568        0.0        0.0        0.0        0.0        0.0        0.0   
10569        0.0        0.0        0.0        0.0        0.0        0.0   

       feature_6  feature_7  feature_8  feature_9  ...  feature_9990  \
0            0.0        0.0

In [18]:
final_df.to_csv('final_df.csv', index=False)

In [19]:
import numpy as np
from sklearn.decomposition import TruncatedSVD

# Convert DataFrame to sparse matrix
tfidf_matrix = final_df.values 

# Initialize and apply SVD
n_components = 100
svd = TruncatedSVD(n_components=n_components)
reduced_data = svd.fit_transform(tfidf_matrix)

# Create a DataFrame with the reduced data
reduced_df = pd.DataFrame(reduced_data, columns=[f'Component_{i+1}' for i in range(n_components)])

# Check explained variance
explained_variance = svd.explained_variance_ratio_
cumulative_explained_variance = np.cumsum(explained_variance)

print("Explained Variance Ratio for each component:")
print(explained_variance)

print("\nCumulative Explained Variance Ratio:")
print(cumulative_explained_variance)

# Output the shape of the reduced data
print("\nShape of the reduced data:")
print(reduced_df.shape)


Explained Variance Ratio for each component:
[0.0026222  0.00823878 0.00727261 0.00573423 0.00537645 0.00466584
 0.00434915 0.00419227 0.0040093  0.00370345 0.00352969 0.00348956
 0.00337088 0.00326619 0.00321386 0.0031332  0.00308908 0.00302432
 0.00292675 0.00284052 0.00273927 0.00268314 0.00264834 0.00260991
 0.00259258 0.00254565 0.00249208 0.00244717 0.0024088  0.00234074
 0.00230757 0.00227292 0.00224793 0.00222997 0.00219209 0.00212648
 0.00211134 0.002064   0.00203224 0.00201495 0.00200244 0.00195257
 0.00191704 0.00188943 0.00187332 0.00182809 0.00180112 0.00178077
 0.00172546 0.00171232 0.0017015  0.00167117 0.0016616  0.00163583
 0.00162232 0.00159703 0.00157759 0.00156481 0.00153797 0.0015302
 0.00151868 0.00150426 0.0014432  0.00144349 0.00143341 0.00141804
 0.00141175 0.00140724 0.00136599 0.00135683 0.00135566 0.00133496
 0.00133186 0.00132638 0.0013188  0.00130714 0.00128478 0.0012772
 0.00127306 0.00126492 0.00125166 0.00123976 0.00122016 0.00120722
 0.00120333 0.00118

In [20]:
print(reduced_df)

       Component_1  Component_2  Component_3  Component_4  Component_5  \
0         0.257484    -0.476793     0.530807    -0.209295    -0.018774   
1         0.258144    -0.478909     0.530993    -0.209383    -0.020397   
2         0.258443    -0.512049     0.483380    -0.254896    -0.038202   
3         0.246473    -0.517603     0.568756    -0.242334    -0.032626   
4         0.305794    -0.423086     0.488995    -0.165515     0.059026   
...            ...          ...          ...          ...          ...   
10565     0.362992     0.230472     0.145405    -0.096038     0.141805   
10566     0.370004     0.252923     0.128625    -0.136340     0.146223   
10567     0.348043     0.187574     0.088294    -0.078362     0.058595   
10568     0.308342     0.123803     0.016121    -0.058103    -0.013721   
10569     0.340053     0.210410     0.101710    -0.111169     0.096915   

       Component_6  Component_7  Component_8  Component_9  Component_10  ...  \
0        -0.017551    -0.144207

In [21]:
reduced_df.to_csv('reduced_df.csv', index=False)

In [24]:
import numpy as np
import pandas as pd

def calculate_class_centroids(reduced_df, labels_df):
    # Ensure labels are strings to avoid issues with complex types
    labels = labels_df['answers'].astype(str).values
    unique_classes = np.unique(labels)
    class_centroids = {}

    for cls in unique_classes:
        class_vectors = reduced_df[labels == cls].values
        centroid = np.mean(class_vectors, axis=0)
        class_centroids[cls] = centroid

    return class_centroids

def calculate_class_spreads(reduced_df, labels_df):
    # Ensure labels are strings to avoid issues with complex types
    labels = labels_df['answers'].astype(str).values
    unique_classes = np.unique(labels)
    class_spreads = {}

    for cls in unique_classes:
        class_vectors = reduced_df[labels == cls].values
        spread = np.std(class_vectors, axis=0)
        class_spreads[cls] = spread

    return class_spreads

def calculate_distances_between_centroids(class_centroids):
    from itertools import combinations

    distances = {}
    for (cls1, centroid1), (cls2, centroid2) in combinations(class_centroids.items(), 2):
        distance = np.linalg.norm(centroid1 - centroid2)
        distances[(cls1, cls2)] = distance

    return distances

In [25]:

labels_df = pd.DataFrame(data, columns=['answers'])

# Calculate class centroids
class_centroids = calculate_class_centroids(reduced_df, labels_df)
print("Class Centroids:")
for cls, centroid in class_centroids.items():
    print(f"Class {cls} centroid: {centroid}")

# Calculate class spreads
class_spreads = calculate_class_spreads(reduced_df, labels_df)
print("\nClass Spreads:")
for cls, spread in class_spreads.items():
    print(f"Class {cls} spread: {spread}")

# Calculate distances between class centroids
distances = calculate_distances_between_centroids(class_centroids)
print("\nDistances Between Class Centroids:")
for (cls1, cls2), distance in distances.items():
    print(f"Distance between class {cls1} and class {cls2}: {distance}")

Class Centroids:
Class [{'answer_start': 0, 'text': "Kenya's inclusion among the beneficiaries of the US Government's African Growth and Opportunity Act (AGOA)"}, {'answer_start': 101, 'text': 'AGOA'}, {'answer_start': 65, 'text': 'African Growth and Opportunity Act'}] centroid: [ 0.25842006  0.01852621 -0.02247142 -0.02685333 -0.05835994  0.04408099
  0.05097985  0.01993164 -0.01714699 -0.05566612 -0.07254025 -0.01403631
 -0.01747953 -0.07131489  0.00071431  0.06768913 -0.00469978 -0.01186837
 -0.02393101 -0.02507229 -0.07005647  0.04932809 -0.07315802 -0.04334198
  0.02089192  0.00089721  0.04779698  0.04777786 -0.06240562  0.05300642
  0.01395268  0.06914046 -0.03037683  0.04575392  0.03844334  0.02002042
 -0.06073249  0.04745377  0.01608461  0.0327767   0.00079811 -0.03274295
 -0.03264294  0.07112023  0.04280684  0.00425109 -0.00157629  0.01187981
  0.01550338 -0.06856506 -0.00742352  0.02646873 -0.05083563 -0.03059017
 -0.01294605  0.02407787  0.00571594 -0.02985597 -0.1055268   0

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Class [{'answer_start': 428, 'text': 'Tesla and/or Edison had refused the prize'}, {'answer_start': 428, 'text': 'Tesla and/or Edison had refused the prize'}, {'answer_start': 428, 'text': 'Tesla and/or Edison had refused the prize'}] centroid: [ 2.82252618e-01 -1.00660856e-01 -1.09501172e-01 -4.18639130e-02
  1.63809033e-01  5.59045369e-02  4.76899493e-02 -1.81049258e-01
 -6.81056441e-02  2.10341393e-02 -2.72227833e-02 -4.17762820e-02
  2.76554395e-02  3.22479052e-05  1.49292823e-03  1.32024705e-02
 -3.96302179e-02  2.83283110e-02  1.30917602e-02  1.85886759e-03
 -1.76575841e-02  3.14876187e-02 -5.45494726e-02 -9.19247614e-03
 -1.51098783e-03  4.67907385e-03 -3.92472568e-02 -3.95663389e-02
 -1.29659554e-02  5.41784721e-02  3.04419766e-02  9.42606044e-04
 -5.79926051e-03  1.08092722e-03 -3.96755696e-02  6.68710637e-03
 -2.99913016e-03 -6.31068966e-02 -4.55362623e-02  4.59126963e-02
 -1.31820084e-02  4.01720547e-02  3.49164243e-02 -2.68270368e-02
 -8.82185693e-03  2.61820672e-03 -1.7788

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)




Class Spreads:
Class [{'answer_start': 0, 'text': "Kenya's inclusion among the beneficiaries of the US Government's African Growth and Opportunity Act (AGOA)"}, {'answer_start': 101, 'text': 'AGOA'}, {'answer_start': 65, 'text': 'African Growth and Opportunity Act'}] spread: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
Class [{'answer_start': 0, 'text': "Kenya's various ethnic groups typically speak their mother tongues within their own communities"}, {'answer_start': 52, 'text': 'mother tongues'}, {'answer_start': 52, 'text': 'mother tongues'}] spread: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Class [{'answer_start': 91, 'text': '3D printing technology'}, {'answer_start': 91, 'text': '3D printing technology'}, {'answer_start': 79, 'text': 'advances in 3D printing technology'}] spread: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
Class [{'answer_start': 91, 'text': '9.8 million'}, {'answer_start': 91, 'text': '9.8 million'}, {'answer_start': 91, 'text': '9.8 million'}] spread: [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
Class [{'answer_start': 91, 'text': 'Chicag

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

